In [1]:
import pandas as pd
from tqdm import tqdm, trange

In [2]:
url = "https://raw.githubusercontent.com/HipsterVizNinja/random-data/main/Music/hot-100/Hot%20100.csv"
df = pd.read_csv(url)

We need to take the row where the "time on the chart" is greatest as that will capture the highest, lowest and length of position on chart. We may lose sight ofsongs that have come onto the chart and left then come back. We could check that by ordering by artist and date then taking the dat difference.if the date difference between 2 consecutive entries is greater than 1 week, then it left and came back. We can address this down the line.

In [3]:
# with this method it has taken the max value in the column of each row grouped by song_id. it results in peak position being incorrect. No impact as the moment. to be considered in future EDA
df_singles = df.groupby('song_id').max()

In [4]:
#add index, drop unnecessary columns

df_singles.reset_index(inplace = True)
df_singles.drop(['chart_url', 'peak_position', 'previous_week', 'instance'], axis =1, inplace=True)

In [5]:
df_singles.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 30444 entries, 0 to 30443
Data columns (total 9 columns):
 #   Column             Non-Null Count  Dtype  
---  ------             --------------  -----  
 0   song_id            30444 non-null  object 
 1   chart_position     30444 non-null  int64  
 2   chart_date         30444 non-null  object 
 3   song               30444 non-null  object 
 4   performer          30444 non-null  object 
 5   time_on_chart      30444 non-null  int64  
 6   consecutive_weeks  27316 non-null  float64
 7   worst_position     30444 non-null  int64  
 8   chart_debut        30444 non-null  object 
dtypes: float64(1), int64(3), object(5)
memory usage: 2.1+ MB


In [6]:
# check for duplicates in the song column
df_singles['song'].nunique()

25225

In [7]:
df_singles['song_id'].nunique()

30444

### Song Lyric API

From here we need to find an appropriate API to iterate through the dataframe from each song and pull the song lyrics and if possible genre. and add to the dataframe as a column. It might be easier to save as json or csv then iterate and append the results to a new data frame. then append the billboard data after the fact. 

Step 1: Choose an API

In [8]:
# remember to go back and set api token as an environment variable
import lyricsgenius

genius = lyricsgenius.Genius('A7Ay4wVnG3d6Axz0UCLBFKdK-HKpi14m9jXMuGj3xvOFZIRN5mSIUNXr8dW0grBd')

In [9]:
artist = genius.search_artist("Red hot chilli peppers", max_songs=3, sort="title")

Searching for songs by Red hot chilli peppers...

Changing artist name to 'Red Hot Chili Peppers'
Song 1: "1970"
Song 2: "21 Century"
Song 3: "21st Century"

Reached user-specified song limit (3).
Done. Found 3 songs.


In [10]:
song = artist.song("By the way")

Searching for "By the way" by Red Hot Chili Peppers...
Done.


In [11]:
song.lyrics

"By the Way Lyrics[Chorus]\nStanding in line to see the show tonight\nAnd there's a light on, heavy glow\nBy the way, I tried to say\nI'd be there waiting for\nDani, the girl, is singing songs to me\nBeneath the marquee, overload\n\n[Verse 1]\nSteak knife, card shark\nCon job, boot cut\nSkin that flick, she's such a little DJ\nGet there quick by street but not the freeway\nTurn that trick to make a little leeway\nBeat that nic, but not the way that we play\nDogtown, blood bath\nRib cage, soft tail\n[Chorus]\nStanding in line to see the show tonight\nAnd there's a light on, heavy glow\nBy the way, I tried to say\nI'd be there waiting for\n\n[Verse 2]\nBlack jack, dope dick\nPawn shop, quick pick\nKiss that dyke, I know you want to hold one\nNot on strike but I'm about to bowl one\nBite that mic, I know you never stole one\nGirls that like a story, so I told one\nSong bird, main line\nCash back, hard top\n\n[Chorus]\nStanding in line to see the show tonight\nAnd there's a light on, heavy

In [12]:
# song lyric search
genius.search_song("By the way", "Red Hot Chilli Pepers").lyrics

Searching for "By the way" by Red Hot Chilli Pepers...
Done.


"By the Way Lyrics[Chorus]\nStanding in line to see the show tonight\nAnd there's a light on, heavy glow\nBy the way, I tried to say\nI'd be there waiting for\nDani, the girl, is singing songs to me\nBeneath the marquee, overload\n\n[Verse 1]\nSteak knife, card shark\nCon job, boot cut\nSkin that flick, she's such a little DJ\nGet there quick by street but not the freeway\nTurn that trick to make a little leeway\nBeat that nic, but not the way that we play\nDogtown, blood bath\nRib cage, soft tail\n[Chorus]\nStanding in line to see the show tonight\nAnd there's a light on, heavy glow\nBy the way, I tried to say\nI'd be there waiting for\n\n[Verse 2]\nBlack jack, dope dick\nPawn shop, quick pick\nKiss that dyke, I know you want to hold one\nNot on strike but I'm about to bowl one\nBite that mic, I know you never stole one\nGirls that like a story, so I told one\nSong bird, main line\nCash back, hard top\n\n[Chorus]\nStanding in line to see the show tonight\nAnd there's a light on, heavy

In [13]:
# API request function

def get_lyrics(title, artist):
    ''' 
	Function to return lyrics of each song using Genius API
	'''
    try:
        return genius.search_song(title, artist).lyrics
    except:
        return 'not found'

In [14]:
30444/10

3044.4

In [15]:
q1 = df_singles.iloc[0:3044]
q2 = df_singles.iloc[3044:6088]
q3 = df_singles.iloc[6088:9132]
q4 = df_singles.iloc[9132:12176]
q5 = df_singles.iloc[12176:15220]
q6 = df_singles.iloc[15220:18264]
q7 = df_singles.iloc[18264:21308]
q8 = df_singles.iloc[21308:24352]
q9 = df_singles.iloc[24352:27396]
q10 = df_singles.iloc[27396:-1]

In [16]:
#lyrics_1 = q1.apply(lambda row: get_lyrics(row['song'], row['performer']), axis =1)

In [17]:
#q1['lyrics'] = lyrics_1

#from pathlib import Path 
#filepath = Path('./data/q1.csv')  
#q1.to_csv(filepath)

In [18]:
#q1.head()

In [19]:
tqdm.pandas(desc='prog bar')

In [20]:
lyrics_2= q2.progress_apply(lambda row: get_lyrics(row['song'], row['performer']), axis =1)

prog bar:   0%|          | 0/3044 [00:00<?, ?it/s]

Searching for "Blue Moon" by Herb Lance & The Classics...


prog bar:   0%|          | 2/3044 [00:00<20:14,  2.50it/s]

Done.
Searching for "Blue Moon" by The Marcels...


prog bar:   0%|          | 3/3044 [00:01<28:36,  1.77it/s]

...

Done.
Searching for "Don't Let It End" by Styx...


prog bar: 100%|██████████| 3044/3044 [57:19<00:00,  2.23s/it]

Done.
Searching for "Don't Let It Get You Down" by The Crusaders...


prog bar: 100%|██████████| 3044/3044 [57:19<00:00,  1.13s/it]

Specified song does not contain lyrics. Rejecting.


In [22]:
from pathlib import Path 
q2['lyrics'] = lyrics_2

filepath = Path('./data/q2.csv')  
q2.to_csv(filepath)

/var/folders/w6/sy887bgd32s1j5gq5fj42l000000gn/T/ipykernel_6659/3673470095.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  q2['lyrics'] = lyrics_2


In [23]:
lyrics_3 = q3.progress_apply(lambda row: get_lyrics(row['song'], row['performer']), axis =1)

prog bar:   0%|          | 0/3044 [00:00<?, ?it/s]

Searching for "Don't Let It Go To Your Head" by Brand Nubian...


prog bar:   0%|          | 2/3044 [00:03<1:36:10,  1.90s/it]

Done.
Searching for "Don't Let It Show" by The Alan Parsons Project...


prog bar:   0%|          | 3/3044 [00:05<1:35:27,  1.88s/it]

...

Done.
Searching for "Gravy Waltz" by Steve Allen...


prog bar: 100%|██████████| 3044/3044 [1:39:02<00:00,  1.89s/it]

Done.
Searching for "Grazing In The Grass" by Hugh Masekela...


prog bar: 100%|██████████| 3044/3044 [1:39:03<00:00,  1.95s/it]

Specified song does not contain lyrics. Rejecting.


In [24]:
q3['lyrics'] = lyrics_3

filepath = Path('./data/q3.csv')  
q3.to_csv(filepath)

/var/folders/w6/sy887bgd32s1j5gq5fj42l000000gn/T/ipykernel_6659/2965666441.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  q3['lyrics'] = lyrics_3


In [25]:
lyrics_4 = q4.progress_apply(lambda row: get_lyrics(row['song'], row['performer']), axis =1)

prog bar:   0%|          | 0/3044 [00:00<?, ?it/s]

Searching for "Grazing In The Grass" by The Friends Of Distinction...


prog bar:   0%|          | 2/3044 [00:01<46:04,  1.10it/s]

Done.
Searching for "Grease" by Frankie Valli...


prog bar:   0%|          | 3/3044 [00:05<1:42:53,  2.03s/it]

...

Done.
Searching for "I'll Never Find Another You" by Sonny James...


prog bar: 100%|██████████| 3044/3044 [1:35:27<00:00,  2.16s/it]

Done.
Searching for "I'll Never Find Another You" by The Seekers...


prog bar: 100%|██████████| 3044/3044 [1:35:29<00:00,  1.88s/it]

Done.


In [26]:
q4['lyrics'] = lyrics_4

filepath = Path('./data/q4.csv')  
q4.to_csv(filepath)

/var/folders/w6/sy887bgd32s1j5gq5fj42l000000gn/T/ipykernel_6659/657489739.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  q4['lyrics'] = lyrics_4


In [27]:
lyrics_5 = q5.progress_apply(lambda row: get_lyrics(row['song'], row['performer']), axis =1)

prog bar:   0%|          | 0/3044 [00:00<?, ?it/s]

Searching for "I'll Never Get Over You (Getting Over Me)" by Expose...


prog bar:   0%|          | 2/3044 [00:01<33:38,  1.51it/s]

Done.
Searching for "I'll Never Let You Go" by Steelheart...


prog bar:   0%|          | 3/3044 [00:02<52:34,  1.04s/it]

...

Done.
Searching for "Little Darlin'" by Sheila...


prog bar: 100%|██████████| 3044/3044 [1:41:05<00:00,  1.80s/it]

Done.
Searching for "Little Darling (i Need You)" by The Doobie Brothers...


prog bar: 100%|██████████| 3044/3044 [1:41:07<00:00,  1.99s/it]

Done.


In [28]:
q5['lyrics'] = lyrics_5

filepath = Path('./data/q5.csv')  
q5.to_csv(filepath)

/var/folders/w6/sy887bgd32s1j5gq5fj42l000000gn/T/ipykernel_6659/563832898.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  q5['lyrics'] = lyrics_5


In [29]:
lyrics_6 = q6.progress_apply(lambda row: get_lyrics(row['song'], row['performer']), axis =1)

prog bar:   0%|          | 0/3044 [00:00<?, ?it/s]

Searching for "Little Darling, I Need You" by Marvin Gaye...


prog bar:   0%|          | 2/3044 [00:03<1:26:44,  1.71s/it]

Done.
Searching for "Little Deuce Coupe" by The Beach Boys...


prog bar:   0%|          | 3/3044 [00:04<1:22:32,  1.63s/it]

...

Done.
Searching for "No Tears Left To Cry" by Ariana Grande...


prog bar: 100%|██████████| 3044/3044 [1:44:38<00:00,  3.58s/it]

Searching for "No Tell Lover" by Chicago...


prog bar: 100%|██████████| 3044/3044 [1:44:42<00:00,  2.06s/it]

Done.


In [30]:
q6['lyrics'] = lyrics_6

filepath = Path('./data/q6.csv')  
q6.to_csv(filepath)

/var/folders/w6/sy887bgd32s1j5gq5fj42l000000gn/T/ipykernel_6659/913627939.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  q6['lyrics'] = lyrics_6


In [31]:
lyrics_7 = q7.progress_apply(lambda row: get_lyrics(row['song'], row['performer']), axis =1)

prog bar:   0%|          | 0/3044 [00:00<?, ?it/s]

Searching for "No Tellin'" by Drake...


prog bar:   0%|          | 2/3044 [00:03<1:30:33,  1.79s/it]

Done.
Searching for "No Tengo Dinero" by Los Umbrellos...


prog bar:   0%|          | 3/3044 [00:04<1:21:57,  1.62s/it]

...

Done.
Searching for "Sandcastles" by Beyonce...


prog bar: 100%|██████████| 3044/3044 [1:41:46<00:00,  2.08s/it]

Done.
Searching for "Sandra's Rose" by Drake...


prog bar: 100%|██████████| 3044/3044 [1:41:49<00:00,  2.01s/it]

Done.


In [32]:
q7['lyrics'] = lyrics_7

filepath = Path('./data/q7.csv')  
q7.to_csv(filepath)

/var/folders/w6/sy887bgd32s1j5gq5fj42l000000gn/T/ipykernel_6659/3693663449.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  q7['lyrics'] = lyrics_7


In [33]:
lyrics_8 = q8.progress_apply(lambda row: get_lyrics(row['song'], row['performer']), axis =1)

prog bar:   0%|          | 0/3044 [00:00<?, ?it/s]

Searching for "Sandstorm" by Darude...


prog bar:   0%|          | 2/3044 [00:01<33:34,  1.51it/s]

Done.
Searching for "Sandy" by Dion...


prog bar:   0%|          | 3/3044 [00:03<1:14:26,  1.47s/it]

...

Done.
Searching for "Take You Dancing" by Jason Derulo...


prog bar: 100%|██████████| 3044/3044 [1:42:10<00:00,  1.47s/it]

Done.
Searching for "Take You Down" by Chris Brown...


prog bar: 100%|██████████| 3044/3044 [1:42:11<00:00,  2.01s/it]

Done.


In [34]:
q8['lyrics'] = lyrics_8

filepath = Path('./data/q8.csv')  
q8.to_csv(filepath)

/var/folders/w6/sy887bgd32s1j5gq5fj42l000000gn/T/ipykernel_6659/4197339293.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  q8['lyrics'] = lyrics_8


In [35]:
lyrics_9 = q9.progress_apply(lambda row: get_lyrics(row['song'], row['performer']), axis =1)

prog bar:   0%|          | 0/3044 [00:00<?, ?it/s]

Searching for "Take You Home With Me a.k.a. Body" by R. Kelly & Jay-Z...


prog bar:   0%|          | 2/3044 [00:01<36:38,  1.38it/s]

Done.
Searching for "Take You Home" by Angie Martinez Featuring Kelis...


prog bar:   0%|          | 3/3044 [00:02<47:55,  1.06it/s]

...

Done.
Searching for "Unstoppable" by Rascal Flatts...


prog bar: 100%|██████████| 3044/3044 [1:39:30<00:00,  1.75s/it]

Done.
Searching for "Unstoppable" by Sia...


prog bar: 100%|██████████| 3044/3044 [1:39:31<00:00,  1.96s/it]

Done.


In [36]:
q9['lyrics'] = lyrics_9

filepath = Path('./data/q9.csv')  
q9.to_csv(filepath)

/var/folders/w6/sy887bgd32s1j5gq5fj42l000000gn/T/ipykernel_6659/1654076019.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  q9['lyrics'] = lyrics_9


In [37]:
lyrics_10 = q10.progress_apply(lambda row: get_lyrics(row['song'], row['performer']), axis =1)

prog bar:   0%|          | 0/3047 [00:00<?, ?it/s]

Searching for "Untie Me" by The Tams...


prog bar:   0%|          | 2/3047 [00:02<59:06,  1.16s/it]

Done.
Searching for "Until I Bleed Out" by The Weeknd...


prog bar:   0%|          | 3/3047 [00:03<1:00:53,  1.20s/it]

...

Done.
Searching for "whoknows" by Musiq...


prog bar: 100%|██████████| 3047/3047 [1:39:36<00:00,  1.76s/it]

Done.
Searching for "www.memory" by Alan Jackson...


prog bar: 100%|██████████| 3047/3047 [1:39:39<00:00,  1.96s/it]

Done.


In [38]:
q10['lyrics'] = lyrics_10

filepath = Path('./data/q10.csv')  
q10.to_csv(filepath)

/var/folders/w6/sy887bgd32s1j5gq5fj42l000000gn/T/ipykernel_6659/2132313872.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  q10['lyrics'] = lyrics_10


In [43]:
num_not_found = sum(q5['lyrics'] == 'not found')
total = len(q5)
pct_not_found = num_not_found / total
pct_not_found

0.07293035479632064

In [ ]:
q1['lyrics'] == 'not found'